
# EDA automático con **ydata‑profiling** (Pandas Profiling) — *Titanic*
> Notebook listo para ejecutar sobre `titanic.csv` (debe estar en la misma carpeta que este notebook).  
> Funciona en Jupyter local o Google Colab.

**Qué hace:** instala dependencias, carga el dataset, genera un informe HTML y lo muestra embebido en el notebook.


## 1) Instalar dependencias

In [9]:
%pip install ipywidgets

   ---------------------------------------- 0.0/2.2 MB ? eta -:--:--
   ---------------------------- ----------- 1.6/2.2 MB 7.6 MB/s eta 0:00:01
   ---------------------------------------- 2.2/2.2 MB 6.9 MB/s  0:00:00

   -------------------------- ------------- 2/3 [ipywidgets]
   ---------------------------------------- 3/3 [ipywidgets]

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 25.3
[notice] To update, run: C:\Users\usain\Desktop\Lujan\Curso Python\.venv\Scripts\python.exe -m pip install --upgrade pip


In [4]:
%pip install --upgrade setuptools

   ---------------------------------------- 0.0/1.2 MB ? eta -:--:--
   -------- ------------------------------- 0.3/1.2 MB ? eta -:--:--
   ---------------------------------------- 1.2/1.2 MB 4.3 MB/s  0:00:00
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 25.3
[notice] To update, run: C:\Users\usain\Desktop\Lujan\Curso Python\.venv\Scripts\python.exe -m pip install --upgrade pip


In [10]:
# Si estás en Google Colab o Jupyter, ejecuta esta celda una vez
# Nota: usa %pip (mágica de Jupyter) para instalar dentro del entorno del kernel
%pip install -U ydata-profiling pandas matplotlib numpy


  Using cached matplotlib-3.10.7-cp312-cp312-win_amd64.whl.metadata (11 kB)
  Using cached numpy-2.3.4-cp312-cp312-win_amd64.whl.metadata (60 kB)
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 25.3
[notice] To update, run: C:\Users\usain\Desktop\Lujan\Curso Python\.venv\Scripts\python.exe -m pip install --upgrade pip


## 2) Imports

In [11]:
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
from IPython.display import display, HTML
from pathlib import Path

print("Versiones:")
import sys, importlib
print("Python:", sys.version.split()[0])
print("pandas:", pd.__version__)
import matplotlib
print("matplotlib:", matplotlib.__version__)
import ydata_profiling
print("ydata_profiling:", ydata_profiling.__version__)


Versiones:
Python: 3.12.10
pandas: 2.3.3
matplotlib: 3.10.0
ydata_profiling: v4.17.0


## 3) Cargar `titanic.csv`

In [12]:
# Asegúrate de que 'titanic.csv' esté en la misma carpeta que este notebook.
csv_path = Path("titanic.csv")
assert csv_path.exists(), "No se encontró 'titanic.csv' en el directorio actual."

df = pd.read_csv(csv_path)
print("Shape:", df.shape)
display(df.head())


Shape: (891, 12)


PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

## 4) Reporte EDA básico (modo explorativo)

In [13]:
# Genera un informe completo. 'explorative=True' habilita análisis extra (recomendado).
profile = ProfileReport(
    df,
    title="Titanic — EDA automático (ydata‑profiling)",
    explorative=True
)

# 4.a) Mostrar el reporte incrustado (iframe) directamente en el notebook
profile.to_notebook_iframe()

# 4.b) Guardar a HTML para compartir
output_html = "eda_titanic_report.html"
profile.to_file(output_html)
print(f"Reporte guardado en: {output_html}")


Render HTML: 100%|██████████| 1/1 [00:01<00:00,  1.77s/it]


Export report to file: 100%|██████████| 1/1 [00:00<00:00, 37.99it/s]

Reporte guardado en: eda_titanic_report.html



## 5) Configuraciones útiles (performance y privacidad)

Si el dataset es grande o quieres acelerar el análisis, puedes:
- Desactivar algunos cálculos pesados (correlaciones de alta complejidad).
- Tomar una muestra de filas.
- Enmascarar variables sensibles.

Las celdas siguientes muestran ejemplos.


In [ ]:
# (Opcional) Tomar una muestra para acelerar el reporte en datasets grandes
# Descomenta para usar:
# df_sample = df.sample(n=20000, random_state=42) if len(df) > 20000 else df.copy()
# print("Usando muestra con shape:", df_sample.shape)
# base_df = df_sample

# En este notebook, usamos el df completo:
base_df = df


In [ ]:
# (Opcional) Desactivar correlaciones costosas y ajustar configuración
from ydata_profiling.config import Config, Settings

cfg = Settings()
# Desactivar/ajustar correlaciones pesadas
cfg.correlations = Settings().correlations
cfg.correlations.auto = True  # deja que el paquete decida según tamaño
cfg.correlations.spearman.calculate = True
cfg.correlations.kendall.calculate = False  # más lento
cfg.correlations.phik.calculate = False     # puede ser costoso en datasets grandes

# (Opcional) Ajustes de sensibilidad/privacidad (por si tienes columnas personales)
cfg.vars.num.low_categorical_threshold = 5

profile_fast = ProfileReport(
    base_df,
    title="Titanic — EDA (configuración optimizada)",
    explorative=True,
    config=cfg
)
profile_fast.to_file("eda_titanic_report_fast.html")
print("Reporte (rápido) guardado en: eda_titanic_report_fast.html")
profile_fast.to_notebook_iframe()


## 6) Versión mínima (solo lo esencial)

In [ ]:
# Una versión aún más ligera, útil para inspecciones rápidas.
profile_min = ProfileReport(
    base_df.sample(min(len(base_df), 5000), random_state=42),  # muestrea hasta 5k filas
    title="Titanic — EDA (mínimo)",
    explorative=False,            # reporte más simple
    minimal=True                  # desactiva cálculos pesados
)
profile_min.to_file("eda_titanic_report_min.html")
print("Reporte (mínimo) guardado en: eda_titanic_report_min.html")
profile_min.to_notebook_iframe()


## 7) Exportar / Notas finales

In [ ]:
# Archivos generados:
# - eda_titanic_report.html        (completo)
# - eda_titanic_report_fast.html   (optimizado)
# - eda_titanic_report_min.html    (mínimo)

# Sugerencias:
# - Comparte el HTML con tu equipo.
# - Usa los hallazgos (missing values, correlaciones, tipos) para guiar limpieza y feature engineering.
# - Si trabajas con una variable objetivo (p.ej. 'Survived'), considera graficar cruces específicos manualmente.

print("Listo. Revisa los HTML generados en el directorio de trabajo.")



---
*Generado automáticamente — 2025-10-28 20:15:25*  
Si necesitas la versión para otro dataset, cambia el nombre del archivo en la celda de carga.
